In [11]:
import pandas as pd
import numpy as np
from datetime import timedelta

from zigzag import *

import os
import pickle
from config import BASE_DIR
print(os.getcwd())
os.chdir(BASE_DIR)
import scripts.functions as fn 
from scripts.indicators import zigzag, fibonacci_levels, resample, join_after_resample, supertrend




C:\Users\lbisa\Mi unidad (leonardo.bisaro@gmail.com)\Cripto\python\trd_app


In [12]:
klines_file  = './backtest/klines/1h04/Completo_BTCUSDT_1h04_2021-01-01_2023-07-31.DataFrame'
klines_file  = './backtest/klines/1h01/Completo_BTCUSDT_1h01_2021-01-01_2023-07-31.DataFrame'
klines_file = './backtest/klines/2d01/Lateral_BTCUSDT_2d01_2023-06-20_2023-10-09.DataFrame'
klines_file  = './backtest/klines/2d01/Completo_BTCUSDT_2d01_2021-01-01_2023-07-31.DataFrame'
klines_file  = './backtest/klines/2d01/Full_BTCUSDT_2d01_2019-01-01_2024-06-20.DataFrame'
klines_file  = './backtest/klines/1h01/Full_BTCUSDT_1h01_2019-01-01_2024-06-20.DataFrame'

klines_file  = './backtest/klines/1h01/Completo_BNBUSDT_1h01_2021-01-01_2023-07-31.DataFrame'

with open(klines_file, 'rb') as file:
    df = pickle.load(file)
    #data.set_index('datetime',inplace=True)

#df = fn.ohlc_mirror_v(df)

#Filtrar rango de fechas
#ini = pd.to_datetime('2018-06-26')
#fin = pd.to_datetime('2028-05-01')
#df = df[(df['datetime']>=ini)&(df['datetime']<=fin)]
#df.reset_index(inplace=True)
#df.drop(columns=['index'],inplace=True)


#df.drop(columns=['volume'],inplace=True)


In [16]:
#RESAMPLE
dfR = resample(df,periods=16)
dfR = supertrend(dfR)
dfR['price'] = (dfR['high']+dfR['low']+dfR['open']+dfR['close'])/4
df = join_after_resample(df,dfR['price'],'price_resample')
df = join_after_resample(df,dfR['st_trend'],'st_trend')


In [17]:
df['price'] = (df['high']+df['low']+df['open']+df['close'])/4
deviation = 3
df = zigzag(df, deviation = 3)

df['hl2'] = (df['high']+df['low'])/2
df['ma'] = df['close'].ewm(span=200, adjust=False).mean()
trend_condition = (df['ma'] > df['ma'].shift(1)) & (df['ma'].shift(1) > df['ma'].shift(2)) & (df['ma'].shift(2) > df['ma'].shift(3))
df['ma_trend'] = np.where(trend_condition,1,-1)

counter = {'buy':0, 'sl':0}

df['buy'] = np.nan
df['sell'] = np.nan
last_zz = [0,0]
last_low = None
last_high = None
open_pos = False

for index, row in df.iterrows():
    if row['ZigZag'] is not None:
        last_zz[1] = last_zz[0]
        last_zz[0] = row['ZigZag']

        if last_zz[0] < last_zz[1]:
            last_low = last_zz[0]
            last_high = last_zz[1]
                   
    if last_low is not None and last_high is not None:
        fib_levels = fibonacci_levels(last_high,last_low)

        if open_pos and row['low']<last_low: #El precio bajo del ultimo minimo
            last_low = None
            last_high = None
            open_pos = False
            df.at[index, 'sell'] = row['close']  # Sell signal
            counter['sl'] += 1
        
        elif open_pos and row['close'] > fib_levels['100.0%']:
            #df.at[index, 'sell'] = row['close']  # Sell signal
            last_low = None
            last_high = None
            open_pos = False
                    
        elif not open_pos \
             and row['close'] > last_low \
             and fib_levels['23.6%'] <= row['close'] <= fib_levels['61.8%'] \
             and row['close']>row['ma']:
            df.at[index, 'buy'] = row['close']  # Buy signal
            open_pos = True
            counter['buy'] += 1


        
print('Operaciones: ',counter['buy'])
print('Positivas: ',(counter['buy']-counter['sl']))
print('Negativas: ',counter['sl'])
fibonacci_levels(200,100)

Operaciones:  161
Positivas:  83
Negativas:  78


{'0.0%': 100.0,
 '23.6%': 123.6,
 '38.2%': 138.2,
 '50.0%': 150.0,
 '61.8%': 161.8,
 '78.6%': 178.6,
 '100.0%': 200.0,
 '127.2%': 227.2,
 '161.8%': 261.8}

In [18]:
indicators = [
     {'col': 'price_resample','name': 'price_resample','color': 'yellow','row': 1, 'mode':'lines',},
     #{'col': 'st_trigger','name': 'ST Trigger','color': 'red','row': 1, 'mode':'markers',},
     #{'col': 'st_high','name': 'ST High','color': 'green','row': 1, 'mode':'markers',},
        ]

indicators_out = [
     {'col': 'st_trend','name': 'ST','color': 'white','row': 2, 'mode':'lines',},
        ]

#https://plotly.com/python/reference/scatter/#scatter-marker-symbol
#https://plotly.com/python/reference/scatter/#scatter-marker-symbol
events = [
        #{'df':df,'col':'buy','name': 'BUY','color': 'green','symbol': 'circle-dot' }, 
        #{'df':df,'col':'sell','name': 'SELL','color': 'red','symbol': 'circle-dot' }, 
     ]
fig = fn.ohlc_chart(df,indicators=indicators,indicators_out=indicators_out,events=events) #
fig.show()